In [2]:
import pandas as pd
import matplotlib.pyplot as plt
import geopandas as gpd
from shapely.geometry import Polygon, Point
import pyproj
import warnings
import folium
warnings.filterwarnings('ignore')
%matplotlib inline


In [3]:
data = pd.read_csv('coordinates_data.csv')
data.head()

search_longitude  search_latitude                            arrive  \
0        -58.440447       -34.620694         2021-02-28 15:56:00+00:00   
1        -58.418288       -34.581668  2021-02-13 15:12:45.668000+00:00   
2        -58.208933       -34.831096  2021-01-25 17:45:27.320000+00:00   
3        -58.454943       -34.564354  2021-02-25 11:20:09.755000+00:00   
4        -58.451924       -34.559296         2020-09-17 10:45:00+00:00   

                              leave     search_method  \
0         2021-02-28 17:32:00+00:00            google   
1  2021-02-13 16:12:45.668000+00:00  searchInThisArea   
2  2021-01-25 18:45:27.320000+00:00  searchInThisArea   
3  2021-02-25 12:20:09.755000+00:00  searchInThisArea   
4         2020-09-17 11:00:00+00:00  update_time_home   

                          timestamp  \
0     2021-01-31T19:35:42.438-03:00   
1     2021-02-13T12:13:03.714-03:00   
2     2021-01-25T14:45:44.753-03:00   
3     2021-02-25T08:22:32.254-03:00   
4  2020-09-17T08:13:03.302GMT-03:00   

                                        geometry          x          y  \
0        POINT (-58.44044719999999 -34.62069375) -58.440447 -34.620694   
1  POINT (-58.41828804463148 -34.58166840120946) -58.418288 -34.581668   
2  POINT (-58.20893257856369 -34.83109589037829) -58.208933 -34.831096   
3    POINT (-58.454943113029 -34.56435426830171) -58.454943 -34.564354   
4         POINT (-58.45192389999999 -34.5592956) -58.451924 -34.559296   

      new_x     new_y arrive_date  dayOfWeek  
0  0.097696  0.084863  2021-02-28          6  
1  0.119855  0.123889  2021-02-13          5  
2  0.329210 -0.125539  2021-01-25          0  
3  0.083200  0.141203  2021-02-25          3  
4  0.086219  0.146261  2020-09-17          3

In [4]:
data.drop(columns=['x', 'y', 'dayOfWeek'], inplace=True)

In [5]:
def data_x(x):
    x_column = x/0.002345
    return int(x_column)

def data_y(y): 
    y_column = y/0.004492
    return int(y_column)


In [6]:
data['columnx'] = data["new_x"].map(data_x)
data['columny'] = data["new_y"].map(data_y)


In [7]:
data['tuple_xy'] = list(zip(data.columnx, data.columny))

In [8]:
data = data[data.columny >= 0]
data = data[data.columny <= 39] #nunique de de grid_coordinates_gdf.new_y
data = data[data.columnx >= 0]
data = data[data.columnx <= 80]

In [12]:
map_bsas = folium.Map(location=[-34.600,-58.550])
map_bsas

In [10]:
data.apply(lambda row:folium.CircleMarker(location=[row["search_latitude"], row["search_longitude"]]).add_to(map_bsas), axis=1)
map_bsas


In [10]:
data['arrive'] = pd.to_datetime(data['arrive'])
data['leave'] = pd.to_datetime(data['leave'])


In [11]:
data["year"] = data["arrive"].dt.year
data["month"] = data["arrive"].dt.month
data["day"] = data["arrive"].dt.day
data["hour"] = data["arrive"].dt.hour
data["min"] = data["arrive"].dt.minute
data["weekday"] = data["arrive"].dt.weekday

In [12]:
data

search_longitude  search_latitude                           arrive  \
0           -58.440447       -34.620694        2021-02-28 15:56:00+00:00   
1           -58.418288       -34.581668 2021-02-13 15:12:45.668000+00:00   
3           -58.454943       -34.564354 2021-02-25 11:20:09.755000+00:00   
4           -58.451924       -34.559296        2020-09-17 10:45:00+00:00   
5           -58.463061       -34.618974 2021-02-08 05:38:42.027000+00:00   
...                ...              ...                              ...   
7398        -58.404020       -34.575292        2021-02-22 20:00:00+00:00   
7399        -58.458972       -34.618296 2021-02-08 05:33:27.798000+00:00   
7400        -58.385121       -34.620749 2021-02-06 17:45:46.006000+00:00   
7401        -58.536259       -34.624580 2020-12-21 08:00:54.782000+00:00   
7404        -58.383415       -34.591915 2021-01-23 04:15:18.431000+00:00   

                                leave     search_method  \
0           2021-02-28 17:32:00+00:00            google   
1    2021-02-13 16:12:45.668000+00:00  searchInThisArea   
3    2021-02-25 12:20:09.755000+00:00  searchInThisArea   
4           2020-09-17 11:00:00+00:00  update_time_home   
5    2021-02-08 06:38:42.027000+00:00  searchInThisArea   
...                               ...               ...   
7398        2021-02-22 21:00:00+00:00  searchInThisArea   
7399 2021-02-08 06:33:27.798000+00:00  searchInThisArea   
7400 2021-02-06 18:45:46.006000+00:00  searchInThisArea   
7401        2020-12-21 14:00:00+00:00  update_time_home   
7404 2021-01-23 05:15:18.431000+00:00         this_area   

                             timestamp  \
0        2021-01-31T19:35:42.438-03:00   
1        2021-02-13T12:13:03.714-03:00   
3        2021-02-25T08:22:32.254-03:00   
4     2020-09-17T08:13:03.302GMT-03:00   
5        2021-02-08T02:38:45.031-03:00   
...                                ...   
7398     2021-02-22T07:23:07.499-03:00   
7399     2021-02-08T02:36:12.024-03:00   
7400     2021-02-06T14:46:26.843-03:00   
7401  2020-12-21T10:57:42.699GMT-03:00   
7404  2021-01-23T07:12:43.879GMT-03:00   

                                           geometry     new_x     new_y  \
0           POINT (-58.44044719999999 -34.62069375)  0.097696  0.084863   
1     POINT (-58.41828804463148 -34.58166840120946)  0.119855  0.123889   
3       POINT (-58.454943113029 -34.56435426830171)  0.083200  0.141203   
4            POINT (-58.45192389999999 -34.5592956)  0.086219  0.146261   
5      POINT (-58.4630611538887 -34.61897385423121)  0.075082  0.086583   
...                                             ...       ...       ...   
7398  POINT (-58.40402036905289 -34.57529165865814)  0.134123  0.130265   
7399  POINT (-58.45897246152162 -34.61829565260808)  0.079171  0.087261   
7400  POINT (-58.38512051850557 -34.62074907178535)  0.153022  0.084808   
7401                POINT (-58.5362587 -34.6245804)  0.001884  0.080977   
7404   POINT (-58.3834146335721 -34.59191543650812)  0.154728  0.113642   

     arrive_date  columnx  columny  tuple_xy  year  month  day  hour  min  \
0     2021-02-28       41       18  (41, 18)  2021      2   28    15   56   
1     2021-02-13       51       27  (51, 27)  2021      2   13    15   12   
3     2021-02-25       35       31  (35, 31)  2021      2   25    11   20   
4     2020-09-17       36       32  (36, 32)  2020      9   17    10   45   
5     2021-02-08       32       19  (32, 19)  2021      2    8     5   38   
...          ...      ...      ...       ...   ...    ...  ...   ...  ...   
7398  2021-02-22       57       28  (57, 28)  2021      2   22    20    0   
7399  2021-02-08       33       19  (33, 19)  2021      2    8     5   33   
7400  2021-02-06       65       18  (65, 18)  2021      2    6    17   45   
7401  2020-12-21        0       18   (0, 18)  2020     12   21     8    0   
7404  2021-01-23       65       25  (65, 25)  2021      1   23     4   15   

      weekday  
0           6  
1           5  
3    

## Models


In [74]:
data_features = data[['search_longitude', 'search_latitude', 'weekday', 'hour']]
data_features

search_longitude  search_latitude  weekday  hour
0           -58.440447       -34.620694        6    15
1           -58.418288       -34.581668        5    15
3           -58.454943       -34.564354        3    11
4           -58.451924       -34.559296        3    10
5           -58.463061       -34.618974        0     5
...                ...              ...      ...   ...
7398        -58.404020       -34.575292        0    20
7399        -58.458972       -34.618296        0     5
7400        -58.385121       -34.620749        5    17
7401        -58.536259       -34.624580        0     8
7404        -58.383415       -34.591915        5     4

[5912 rows x 4 columns]

In [75]:
from sklearn.preprocessing import RobustScaler

r_scaler = RobustScaler() # Instanciate Robust Scaler

r_scaler.fit(data_features[['weekday']]) # Fit scaler to feature
r_scaler.fit(data_features[['hour']]) # Fit scaler to feature

data_features['weekday'] = r_scaler.transform(data_features[['weekday']]) #Scale
data_features['hour'] = r_scaler.transform(data_features[['hour']]) #Scale

data_features

search_longitude  search_latitude   weekday      hour
0           -58.440447       -34.620694 -0.777778  0.222222
1           -58.418288       -34.581668 -0.888889  0.222222
3           -58.454943       -34.564354 -1.111111 -0.222222
4           -58.451924       -34.559296 -1.111111 -0.333333
5           -58.463061       -34.618974 -1.444444 -0.888889
...                ...              ...       ...       ...
7398        -58.404020       -34.575292 -1.444444  0.777778
7399        -58.458972       -34.618296 -1.444444 -0.888889
7400        -58.385121       -34.620749 -0.888889  0.444444
7401        -58.536259       -34.624580 -1.444444 -0.555556
7404        -58.383415       -34.591915 -0.888889 -1.000000

[5912 rows x 4 columns]

In [76]:
X = data_features[['weekday', 'hour']]
y = data_features[['search_longitude', 'search_latitude']]

# Random Forest

In [77]:
from sklearn.model_selection import train_test_split
from sklearn.ensemble import RandomForestRegressor
from sklearn.multioutput import MultiOutputRegressor


X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.3, random_state=1)


In [78]:
forest = MultiOutputRegressor(RandomForestRegressor(n_estimators=3, random_state=1))

forest = forest.fit(X_train, y_train)

In [79]:
y_train_pred = forest.predict(X_train)
y_test_pred = forest.predict(X_test)

In [80]:
from sklearn.metrics import mean_squared_error
from sklearn.metrics import r2_score

print("MSE train:{}".format(mean_squared_error(y_train, y_train_pred)))
print("MSE test;{}".format(mean_squared_error(y_test, y_test_pred)))

print("R2 score train:{}".format(r2_score(y_train, y_train_pred)))
print("R2 score test:{}".format(r2_score(y_test, y_test_pred)))

MSE train:0.0007159359697391783
MSE test;0.0007164249011486199
R2 score train:0.14302183955421643
R2 score test:0.10518914689582509
